*Réaliser par : Ahmed Nait Said et Abderraouf Lehanine*



# **BIG DATA PROJET :**
## **Objectifs :**
Regrouper des documents textuels tels que les documents qui partagent le même thème se retrouvent dans le même groupe, et les documents qui portent sur des sujets très différents se trouvent dans des groupes différents.

# **L'installation des différentes bibliothèques et outils :**

In [ ]:
!apt-get update
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://downloads.apache.org/spark/spark-3.3.2/spark-3.3.2-bin-hadoop2.tgz
!tar xf /content/spark-3.3.2-bin-hadoop2.tgz
!pip install -q findspark
!pip install pyspark
!pip install avro-python3
!pip install fastavro
import avro.schema
from fastavro import writer, parse_schema
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-3.3.2-bin-hadoop3.2"
os.environ["PYSPARK_SUBMIT_ARGS"] = "--packages org.apache.spark:spark-avro_2.12:3.3.2 pyspark-shell"

Get:1 https://cloud.r-project.org/bin/linux/ubuntu focal-cran40/ InRelease [3,622 B]
Get:2 http://security.ubuntu.com/ubuntu focal-security InRelease [114 kB]
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu2004/x86_64  InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2004/x86_64  InRelease
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu2004/x86_64  Release
Get:6 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu focal InRelease [18.1 kB]
Hit:7 http://archive.ubuntu.com/ubuntu focal InRelease
Get:8 http://archive.ubuntu.com/ubuntu focal-updates InRelease [114 kB]
Hit:10 http://ppa.launchpad.net/cran/libgit2/ubuntu focal InRelease
Get:11 http://security.ubuntu.com/ubuntu focal-security/main amd64 Packages [2,536 kB]
Hit:12 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu focal InRelease
Get:13 http://archive.ubuntu.com/ubuntu focal-backports InRelease [108 kB]
Hit:14 http://ppa.launchpad.net

# **Mise en place de SparkContext et SparkSession :**

In [ ]:
import findspark

findspark.init("spark-3.3.2-bin-hadoop2")

from pyspark import SparkContext
from pyspark.sql import SparkSession

sc = SparkContext(appName="Avro and Parquet App")
spark = SparkSession.builder.appName("Avro and Parquet App").getOrCreate()

# **Télécharger et Décompresser des données :**

In [ ]:
!wget -q http://qwone.com/~jason/20Newsgroups/20news-19997.tar.gz
!tar xf 20news-19997.tar.gz

# **Charger les données dans deux variables de type RDD :**

In [ ]:
# Les documents de la catégorie “alt.atheism” soient dans un RDD et ceux de “rec.sport.baseball” soient dans un autre RDD
alt_atheism_rdd = sc.wholeTextFiles("20_newsgroups/alt.atheism/*")
rec_sport_baseball_rdd = sc.wholeTextFiles("20_newsgroups/rec.sport.baseball/*")

In [ ]:
# Visualisation des RDDS (juste pour voir)
alt_atheism_rdd.collect()

[('file:/content/20_newsgroups/alt.atheism/53791',
  'Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53791 talk.religion.misc:84109 talk.origins:41079\nNewsgroups: alt.atheism,talk.religion.misc,talk.origins\nPath: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!bb3.andrew.cmu.edu!news.sei.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!zaphod.mps.ohio-state.edu!swrinde!cs.utexas.edu!utnut!torn!nott!cunews!rjg\nFrom: rjg@doe.carleton.ca (Richard Griffith)\nSubject: Re: Burden of Proof\nMessage-ID: <rjg.735427215@wesley>\nSender: news@cunews.carleton.ca (News Administrator)\nOrganization: Dept. of Electronics, Carleton University\nReferences: <C5t5sF.8oz@mentor.cc.purdue.edu> <1r4b59$7hg@aurora.engr.LaTech.edu>\nDate: Wed, 21 Apr 1993 21:20:15 GMT\nLines: 23\n\nIn <1r4b59$7hg@aurora.engr.LaTech.edu> ray@engr.LaTech.edu (Bill Ray) writes:\n\n>If I make a statement, "That God exists, loves me, etc." but in no way\n>insist that you believe it, does that place a burden 

In [ ]:
rec_sport_baseball_rdd.collect()

[('file:/content/20_newsgroups/rec.sport.baseball/104985',
  "Newsgroups: rec.sport.baseball\nPath: cantaloupe.srv.cs.cmu.edu!rochester!udel!gatech!howland.reston.ans.net!zaphod.mps.ohio-state.edu!magnus.acs.ohio-state.edu!dmoney\nFrom: dmoney@magnus.acs.ohio-state.edu (Dean R Money)\nSubject: The Braves will come around...\nMessage-ID: <1993Apr23.193027.26515@magnus.acs.ohio-state.edu>\nSender: news@magnus.acs.ohio-state.edu\nNntp-Posting-Host: bottom.magnus.acs.ohio-state.edu\nOrganization: The Ohio State University\nDate: Fri, 23 Apr 1993 19:30:27 GMT\nLines: 28\n\nTo all the Braves doubters:\n\nDon't worry.  The bats will come alive, and the Braves will come around.\nThe pitching is solid, and as long the Braves don't have serious injuries\nto the starting rotation, they'll continue to pitch well.  Heck, with\nthe five starters on the Braves rotation, they could even sustain an\ninjury to one of the five (I hope this doesn't happen, though).\n\nThe bats are there... Pendleton will 

# **Séparer le corps du message de l'entête. (séparation sur “\n\n”) :**

In [ ]:
# Une fonction simple pour just fair le split
def split_message(record):
    header, body = record[1].split('\n\n', 1)
    return (record[0], header, body)
# Puis on map les RDD
rdd_alt = alt_atheism_rdd.map(split_message)
rdd_rec = rec_sport_baseball_rdd.map(split_message)

In [ ]:
# La visualisation des résultats
dataColl=rdd_rec.collect()
for row in dataColl:
    print("File: " + row[0] + "\n Header: " + row[1])

File: file:/content/20_newsgroups/rec.sport.baseball/104985
 Header: Newsgroups: rec.sport.baseball
Path: cantaloupe.srv.cs.cmu.edu!rochester!udel!gatech!howland.reston.ans.net!zaphod.mps.ohio-state.edu!magnus.acs.ohio-state.edu!dmoney
From: dmoney@magnus.acs.ohio-state.edu (Dean R Money)
Subject: The Braves will come around...
Message-ID: <1993Apr23.193027.26515@magnus.acs.ohio-state.edu>
Sender: news@magnus.acs.ohio-state.edu
Nntp-Posting-Host: bottom.magnus.acs.ohio-state.edu
Organization: The Ohio State University
Date: Fri, 23 Apr 1993 19:30:27 GMT
Lines: 28
File: file:/content/20_newsgroups/rec.sport.baseball/104504
 Header: Newsgroups: rec.sport.baseball
Path: cantaloupe.srv.cs.cmu.edu!das-news.harvard.edu!noc.near.net!howland.reston.ans.net!usenet.ins.cwru.edu!wsu-cs!vela.acs.oakland.edu!cs.uiuc.edu!cs.uiuc.edu!steph
From: steph@cs.uiuc.edu (Dale Stephenson)
Subject: Defensive Averages 1988-1992, Third Base
Message-ID: <C5JJrJ.EM3@cs.uiuc.edu>
Summary: career defensive averages

# **Extraire quelques champs de l'entête, par exemple l'organisation et la catégorie (newsgroups) :**

In [ ]:
# Une fonction pour lire le header des doc, et quand elle arrive à Organization et Newsgroups, elle les sauvegarde dans org et newsgoups
def extract_fields(record):
    fields = record[1].split('\n')
    org = next((f[14:] for f in fields if f.startswith('Organization: ')), None)
    newsgroups = next((f[12:] for f in fields if f.startswith('Newsgroups: ')), None)
    # Certains "newsgroups" ont plusieurs catégories, et dans la prochaine étape, il nous faut qu'on ait 2 "newsgroups". Donc on modifie le résultat de la fonction selon la catégorie
    if 'alt.atheism' in newsgroups:
        newsgroups = 'alt.atheism'
    if 'rec.sport.baseball' in newsgroups:
        newsgroups = 'rec.sport.baseball'
    return (record[0], org, newsgroups, record[2])
# Puis on map les RDD
rdd_alt_2 = rdd_alt.map(extract_fields)
rdd_rec_2 = rdd_rec.map(extract_fields)

In [ ]:
# La visualisation des résultats
dataColl2=rdd_alt_2.collect()
for row in dataColl2:
    print("ORG NAME: " + str(row[1]) + "\n NEWS GRP: " + str(row[2]))

ORG NAME: Dept. of Electronics, Carleton University
 NEWS GRP: alt.atheism
ORG NAME: Case Western Reserve University
 NEWS GRP: alt.atheism
ORG NAME: California Institute of Technology, Pasadena
 NEWS GRP: alt.atheism
ORG NAME: Decision Support Inc.
 NEWS GRP: alt.atheism
ORG NAME: Welch Medical Library
 NEWS GRP: alt.atheism
ORG NAME: None
 NEWS GRP: alt.atheism
ORG NAME: Decision Support Inc.
 NEWS GRP: alt.atheism
ORG NAME: None
 NEWS GRP: alt.atheism
ORG NAME: University of Maryland, College Park
 NEWS GRP: alt.atheism
ORG NAME: Indiana University
 NEWS GRP: alt.atheism
ORG NAME: Siemens-Nixdorf AG
 NEWS GRP: alt.atheism
ORG NAME: sgi
 NEWS GRP: alt.atheism
ORG NAME: sgi
 NEWS GRP: alt.atheism
ORG NAME: Decision Support Inc.
 NEWS GRP: alt.atheism
ORG NAME: Monash University, Melb., Australia.
 NEWS GRP: alt.atheism
ORG NAME: California Institute of Technology, Pasadena
 NEWS GRP: alt.atheism
ORG NAME: ITC, Griffith University, Brisbane, Australia
 NEWS GRP: alt.atheism
ORG NAME: N

# **Fusionner les deux RDD (union) :**

In [ ]:
# Fusionner les deux RDD
rdd = rdd_alt_2.union(rdd_rec_2)

# **Transformer le nouveau RDD obtenu pour que chaque élément soit de type pyspark.sql.Row :**

In [ ]:
from pyspark.sql import Row
rdd_row = rdd.map(lambda x: Row(filename=x[0], org=x[1], newsgroups=x[2], body=x[3]))

# **Créer un objet de type DataFrame à partir du RDD précédent :**

In [ ]:
df = rdd_row.toDF()

# **Sauvegarder la DataFrame au format Avro :**

In [ ]:
import io
# Fair un schéma avro
avro_schema = {
    "type": "record",
    "name": "avro",
    "fields": [
        {"name": "filename", "type": "string"},
        {"name": "org", "type": ["string", "null"]},
        {"name": "newsgroups", "type": ["string", "null"]},
        {"name": "body", "type": "string"},
    ]
}

with io.BytesIO() as avro_output:
    # Convertir la DataFrame en dictionnaire et Utiliser le schéma Avro pour écrire les données dans le fichier avro
    writer(avro_output, avro_schema, df.toPandas().to_dict(orient='records'))
    with open('20newsgroups.avro', 'wb') as f:
        f.write(avro_output.getvalue())

# **Sauvegarder la DataFrame au format Parquet :**

In [ ]:
import pyarrow as pa
import pyarrow.parquet as pq
table = pa.Table.from_pandas(df.toPandas())
pq.write_table(table, '20newsgroups.parquet')

# **Faire une analyse descriptive de la DataFrame obtenue à l'étape précédente :**

In [ ]:
# Vérifier qu’on a bien deux catégories différentes de documents
print(f"newsgroups count: {df.select('newsgroups').distinct().count()}")

newsgroups count: 2


In [ ]:
# Vérifier leur nom
print(f"newsgroups list: {df.select('newsgroups').distinct().show(37,truncate=False)}")

+------------------+
|newsgroups        |
+------------------+
|alt.atheism       |
|rec.sport.baseball|
+------------------+

newsgroups list: None


In [ ]:
# Nombre d'organisations différentes
print(f"organizations count: {df.select('org').distinct().count()}")

organizations count: 486


In [ ]:
from pyspark.sql.functions import length, avg, size, split

# Autres statistiques descriptives
df.describe().show()

# Nombre de documents dans chaque newsgroup
df.groupBy('newsgroups').count().show()

# Longueur moyenne des texts (en caractères)
df.select(avg(length('body'))).show()

# Nombre de documents par organisation
df.groupBy('org').count().orderBy('count', ascending=False).show(truncate=False)

# Nombre moyen de documents par organisation
df.groupBy('org').count().agg(avg('count')).show()


+-------+--------------------+--------------------+------------------+--------------------+
|summary|            filename|                 org|        newsgroups|                body|
+-------+--------------------+--------------------+------------------+--------------------+
|  count|                2000|                1937|              2000|                2000|
|   mean|                null|                null|              null|                null|
| stddev|                null|                null|              null|                null|
|    min|file:/content/20_...| Wright State Uni...|       alt.atheism|\t     MLB Standi...|
|    max|file:/content/20_...|       worldbank.org|rec.sport.baseball||> >|> \n|> >|> H...|
+-------+--------------------+--------------------+------------------+--------------------+

+------------------+-----+
|        newsgroups|count|
+------------------+-----+
|       alt.atheism| 1000|
|rec.sport.baseball| 1000|
+------------------+-----+

+-------

# **Transformation du texte :**


In [ ]:
import string
import nltk
from pyspark.ml.feature import HashingTF, IDF, Tokenizer, StopWordsRemover
from pyspark.sql.functions import lower, col, when, regexp_replace, expr, monotonically_increasing_id


# NLTK's stopwords set
nltk.download('stopwords')
stop_words = set(nltk.corpus.stopwords.words('english'))
stop_words = [word.translate(str.maketrans('', '', string.punctuation)) for word in stop_words]

# Convertir le text en miniscule et suprimer l'espace en tant qu'un mot
df = df.withColumn("body", regexp_replace(lower(col("body")), "[^a-zA-Z\\s]", ""))
df = df.withColumn("body", regexp_replace(col("body"), "\\s+", " "))

# Tokenizer le text
tokenizer = Tokenizer(inputCol="body", outputCol="words")
wordsData = tokenizer.transform(df)

# Afficher les mots
wordsData.select("filename", "words").show(truncate=False)

# Suprimer les "Stop Words" (the, in, else ...) de la list des mots pour bien clustrer les documents
stopwordRemover = StopWordsRemover(inputCol="words", outputCol="filtered_words", stopWords=list(stop_words))
filteredWordsData = stopwordRemover.transform(wordsData).select("filtered_words")

# Ajouter un ID pour pouvoir concaténer les mots filtrés avec notre Data Frame
wordsData = wordsData.withColumn("id", monotonically_increasing_id())
filteredWordsData = filteredWordsData.withColumn("id", monotonically_increasing_id())

# Concaténer les deux column
combinedData = wordsData.join(filteredWordsData, "id", "inner").drop("id")

# Afficher les mots après filtrage
combinedData.select("filename", "filtered_words").show(truncate=False)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


+---------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# **Vérification et analyse des mots obtenus :**

In [ ]:
from pyspark.sql.functions import lower, explode, split, count, sum, lit, collect_list

# Compter l'occurrence de chaque mot dans chaque document
data = combinedData.select(explode("filtered_words").alias("word"), "filename") \
    .groupBy("filename", "word") \
    .agg(sum(lit(1)).alias("count"))

# Obtenir les 10 premiers mots en nombre pour chaque document
topWords = data \
    .orderBy(col("filename"), col("count").desc()) \
    .groupBy("filename") \
    .agg(collect_list("word").alias("top_words"), collect_list("count").alias("top_counts")) \
    .selectExpr("filename", "slice(top_words, 1, 10) as top_words", "slice(top_counts, 1, 10) as top_counts")

# Obtenir les 30 premiers mots au total
overallTopWords = data \
    .groupBy("word") \
    .agg(sum("count").alias("total_count")) \
    .orderBy(col("total_count").desc()) \
    .limit(30) \
    .select("word", "total_count")

# Afficher les 10 premiers mots de chaque document et les 10 premiers mots au total
topWords.show(truncate=False)
overallTopWords.show(30, truncate=False)

22837
+---------------------------------------------+--------------------------------------------------------------------------------------------------+----------------------------------------+
|filename                                     |top_words                                                                                         |top_counts                              |
+---------------------------------------------+--------------------------------------------------------------------------------------------------+----------------------------------------+
|file:/content/20_newsgroups/alt.atheism/51060|[atheists, god, atheism, many, religious, religion, believe, belief, people, even]                |[73, 55, 43, 40, 37, 27, 25, 21, 21, 21]|
|file:/content/20_newsgroups/alt.atheism/51122|[god, evil, good, free, omnipotent, omniscient, choice, one, created, beings]                     |[17, 15, 11, 9, 6, 6, 5, 5, 5, 5]       |
|file:/content/20_newsgroups/alt.atheism/51128|[red, c

# **Créer une représentation vectorielle des documents à l’aide de HashingTF et TF-IDF :**


In [ ]:
# Convertir les mots filtrés à des feature vectors par le HashingTF
hashingTF = HashingTF(inputCol="filtered_words", outputCol="rawFeatures", numFeatures=60)
featurizedData = hashingTF.transform(combinedData)

# Afficher les vecteurs
featurizedData.select("filename", "rawFeatures").show(truncate=False)

+---------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|filename                                     |rawFeatures                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [ ]:
# Convertir les feature vectors de HashingTF par le IDF model
idf = IDF(inputCol="rawFeatures", outputCol="features")
idfModel = idf.fit(featurizedData)
rescaledData = idfModel.transform(featurizedData)

rescaledData.select("filename", "features").show(truncate=False)

+---------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# **Grouper les documents qui ont des représentations vectorielles proches :**


Appliquer le Kmeans sur les features de HashingTF :

In [ ]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.evaluation import ClusteringEvaluator

# Créer un VectorAssembler pour convertir les mots filtrés en vecteurs de fonctionnalités
vectorAssembler = VectorAssembler(inputCols=["rawFeatures"], outputCol="features")
vectors = vectorAssembler.transform(featurizedData).select("filename", "features")

# Instancier le modèle Kmeans avec 2 clusters
kmeans = KMeans().setK(2).setSeed(1)
model = kmeans.fit(vectors)

# Appliquer le modèle sur les données vecteurs
transformed = model.transform(vectors).select("filename", "prediction")

# Regrouper et Afficher le nombre des documents selon les clusters prédits
transformed.groupBy("prediction").count().show()


+----------+-----+
|prediction|count|
+----------+-----+
|         1| 1972|
|         0|   28|
+----------+-----+



Appliquer le Kmeans sur les features de TF-IDF :

In [ ]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator
from pyspark.ml.feature import VectorAssembler

# Créer un VectorAssembler pour convertir les mots filtrés en vecteurs de fonctionnalités
vectorAssembler = VectorAssembler(inputCols=["rawFeatures"], outputCol="features2")
vectors = vectorAssembler.transform(rescaledData).select("filename", "features")

# Instancier le modèle Kmeans avec 2 clusters
kmeans = KMeans().setK(2).setSeed(1)
model = kmeans.fit(vectors)

# Appliquer le modèle sur les données vecteurs
transformed = model.transform(vectors).select("filename", "prediction")

# Regrouper et Afficher le nombre des documents selon les clusters prédits
transformed.groupBy("prediction").count().show()

+----------+-----+
|prediction|count|
+----------+-----+
|         1| 1976|
|         0|   24|
+----------+-----+

